# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [RecurrentPPO]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 16.67 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f3e2ba8e350>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21566.44 , over-consume=kWh  38919.19 , under-consume=kWh  17352.75 , Total_cost=€  906.9 , overcost=€  1394.94 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/RecurrentPPO_VPP_simulator.ipynb"


In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

model_id = "s37o8q0n"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21865.49 , over-consume=kWh  39618.24 , under-consume=kWh  17752.75 , Total_cost=€  898.87 , overcost=€  1404.31 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4123.59 , over-consume=KWh  1973.83 , under-consume=KWh  6097.43 , Total_cost=€  -72.13 , Overcost=€  70.88 
 EV_INFO: Av.EV_energy_leaving=kWh  65.97 , Std.EV_energy_leaving=kWh  26.2 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 389009.55 - Step_rewars (load_t= 360759.82, EVs_energy_t= 6271.65)
 - Final_rewards (EVs_energy= 15475.01, Overconsume= -1217.2, Underconsume= -2689.95, Overcost= 10410.21)
Episode:1 Score:389009.54945360776


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  59.762127  48.793278  70.394096  37.443687   
2022-01-01 00:15:00  59.186543  49.043278  70.644096  36.868103   
2022-01-01 00:30:00  58.681465  49.293278  70.894096  36.363026   
2022-01-01 00:45:00  58.231422  49.543278  71.144096  35.912983   
2022-01-01 01:00:00  57.701988  49.793278  71.394096  35.383549   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00   0.000000  99.989998   0.000000   0.000000   
2022-06-06 05:00:00   0.000000  99.989998   0.000000   0.000000   
2022-06-06 05:15:00   0.000000  99.989998   0.000000   0.000000   
2022-06-06 05:30:00   0.000000  99.989998   0.000000   0.000000   
2022-06-06 05:45:00   0.000000  99.989998  51.302254   0.000000   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 2]   
2022-01-01 00:15:00  [3125, 3127, 3126, 3128]  [2, 1, 1, 2]   
2022-01-01 00:30:00  [3125, 3127, 3126, 3128]  [2, 1, 1, 2]   
2022-01-01 00:45:00  [3125, 3127, 3126, 3128]  [2, 1, 1, 2]   
2022-01-01 01:00:00  [3125, 3127, 3126, 3128]  [2, 1, 1, 2]   
...                                       ...           ...   
2022-06-06 04:45:00           [0, 3585, 0, 0]  [0, 1, 0, 0]   
2022-06-06 05:00:00           [0, 3585, 0, 0]  [0, 1, 0, 0]   
2022-06-06 05:15:00           [0, 3585, 0, 0]  [0, 1, 0, 0]   
2022-06-06 05:30:00           [0, 3585, 0, 0]  [0, 1, 0, 0]   
2022-06-06 05:45:00        [0, 3585, 3586, 0]  [0, 1, 1, 0]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [True, False, False, True]        2.000000   
2022-01-01 00:30:00    [True, False, False, True]        2.000000   
2022-01-01 00:45:00    [True, False, False, True]        2.000000   
2022-01-01 01:00:00    [True, False, False, True]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00      [True, True, True, True]        0.000009   
2022-06-06 05:00:00      [True, True, True, True]        0.000009   
2022-06-06 05:15:00      [True, True, True, True]        0.000009   
2022-06-06 05:30:00      [True, True, True, True]        0.000009   
2022-06-06 05:45:00     [True, False, True, True]        0.000009   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.070304e+00    15.000000        0.0   
2022-01-01 00:15:00          -4.604684  4.440892e-16    15.000000        0.0   
2022-01-01 00:30:00          -4.040616  4.440892e-16    15.000000        0.0   
2022-01-01 00:45:00          -3.600334  0.000000e+00    15.000000        0.0   
2022-01-01 01:00:00          -4.235472  0.000000e+00    15.000000        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00           0.000000 -8.261802e+00   -13.719006        0.0   
2022-06-06 05:00:00           0.000000 -1.359091e+01   -12.724222        0.0   
2022-06-06 05:15:00           0.000000 -1.249664e+01   -11.659014        0.0   
2022-06-06 05:30:00           0.000000 -1.132492e+01   -12.514464        0.0   
2022-06-06 05:45:00           0.000000 -1.226591e+01    -6.565061        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00 -13.719006  
2022-06-06 05:00:00 -12.724222  
2022-06-06 05:15:00 -11.659014  
2022-06-06 05:30:00 -12.514464  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 10:00:00, Parking_time: 24, Leaving_time: 2022-01-02 10:00:00, SOC: 0.46971476624459885, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 18:30:00, Parking_time: 24, Leaving_time: 2023-01-01 18:30:00, SOC: 0.3534072436707165, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12325.53 , over-consume=kWh  34063.96 , under-consume=kWh  21738.43 , Total_cost=€  614.35 , overcost=€  1508.88 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13294.14 , over-consume=kWh  35159.25 , under-consume=kWh  21865.11 , Total_cost=€  634.86 , overcost=€  1523.92 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7340.82 , over-consume=KWh  1100.04 , under-consume=KWh  8440.87 , Total_cost=€  -280.8 , Overcost=€  49.27 
 EV_INFO: Av.EV_energy_leaving=kWh  71.78 , Std.EV_energy_leaving=kWh  25.48 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 384569.21 - Step_rewars (load_t= 335081.93, EVs_energy_t= 21380.55)
 - Final_rewards (EVs_energy= 18199.1, Overconsume= -460.71, Underconsume= -3488.3, Overcost= 13856.65)
Episode:1 Score:384569.2096822797


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  38.510223  89.291779  99.989998  65.262672   
2022-06-06 05:00:00  39.386620  90.168175  99.989998  66.139069   
2022-06-06 05:15:00  40.214504  90.996063  99.989998  66.966957   
2022-06-06 05:30:00  41.125477  91.907036  99.989998  67.877930   
2022-06-06 05:45:00  42.106125  92.887680  99.989998  68.858574   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [0, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [0, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [0, 1, 0, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [6712, 6711, 6710, 6713]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [6712, 6711, 6710, 6713]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [6712, 6711, 6710, 6713]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [6712, 6711, 6710, 6713]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [6712, 6711, 6710, 6713]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00   [True, False, False, True]        0.000000   
2022-01-01 00:45:00   [True, False, False, True]        0.000000   
2022-01-01 01:00:00    [True, False, True, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, True, False, True]        7.626713   
2022-06-06 05:00:00    [True, True, False, True]       10.516777   
2022-06-06 05:15:00    [True, True, False, True]        9.934646   
2022-06-06 05:30:00   [True, False, False, True]       10.931663   
2022-06-06 05:45:00   [True, False, False, True]       11.767782   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.443864    -5.194877        0.0   
2022-01-01 00:15:00                0.0 -4.214365    -5.049170        0.0   
2022-01-01 00:30:00                0.0 -4.054087    -3.718512        0.0   
2022-01-01 00:45:00                0.0 -3.231107    -3.604599        0.0   
2022-01-01 01:00:00                0.0 -3.162759    -5.653440        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0 -2.542226    -4.175968        0.0   
2022-06-06 05:00:00                0.0 -3.505581    -3.852562        0.0   
2022-06-06 05:15:00                0.0 -3.311537    -4.406460        0.0   
2022-06-06 05:30:00                0.0 -3.643876    -4.870971        0.0   
2022-06-06 05:45:00                0.0 -3.922583    -4.934747        0.0   

                      rewards  
time                           
2022-01-01 00:00:00 -5.194877  
2022-01-01 00:15:00 -5.049170  
2022-01-01 00:30:00 -3.718512  
2022-01-01 00:45:00 -3.604599  
2022-01-01 01:00:00 -5.653440  
...                       ...  
2022-06-06 04:45:00 -4.175968  
2022-06-06 05:00:00 -3.852562  
2022-06-06 05:15:00 -4.406460  
2022-06-06 05:30:00 -4.870971  
2022-06-06 05:45:00 -4.934747  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 09:15:00, Parking_time: 22.50992009705091, Leaving_time: 2022-01-02 07:45:35.712349, SOC: 0.5328661297264876, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 22:30:00, Parking_time: 22.4250263600035, Leaving_time: 2023-01-01 20:55:30.094896, SOC: 0.49500095416747303, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8729.91 , over-consume=kWh  32266.77 , under-consume=kWh  23536.86 , Total_cost=€  497.41 , overcost=€  1353.03 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7282.9 , over-consume=kWh  31510.88 , under-consume=kWh  24227.98 , Total_cost=€  437.61 , overcost=€  1316.28 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10219.11 , over-consume=KWh  842.03 , under-consume=KWh  11061.14 , Total_cost=€  -362.76 , Overcost=€  34.96 
 EV_INFO: Av.EV_energy_leaving=kWh  72.94 , Std.EV_energy_leaving=kWh  25.31 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 358542.88 - Step_rewars (load_t= 308972.51, EVs_energy_t= 22874.56)
 - Final_rewards (EVs_energy= 16827.14, Overconsume= -274.36, Underconsume= -4810.2, Overcost= 14953.24)
Episode:1 Score:358542.87970055494


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 03:30:00  33.489239  75.369240  77.960480  0.0   
2022-06-06 03:45:00   0.000000  75.988113  78.579353  0.0   
2022-06-06 04:00:00   0.000000  76.872955  79.464195  0.0   
2022-06-06 04:15:00   0.000000  77.676819  80.268059  0.0   
2022-06-06 04:30:00   0.000000  78.464531  81.055771  0.0   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [1, 1, 1, 1]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [1, 1, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 1, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 1, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 1, 1, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [9831, 9832, 9833, 0]  [2, 1, 1, 0]   
2022-06-06 03:45:00     [0, 9832, 9833, 0]  [2, 1, 1, 0]   
2022-06-06 04:00:00     [0, 9832, 9833, 0]  [2, 1, 1, 0]   
2022-06-06 04:15:00     [0, 9832, 9833, 0]  [2, 1, 1, 0]   
2022-06-06 04:30:00     [0, 9832, 9833, 0]  [2, 1, 1, 0]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00   [False, False, False, True]        0.000000   
2022-01-01 00:30:00    [True, False, False, True]        0.000000   
2022-01-01 00:45:00    [True, False, False, True]        0.000000   
2022-01-01 01:00:00    [True, False, False, True]        0.000000   
...                                           ...             ...   
2022-06-06 03:30:00     [False, True, True, True]        4.965237   
2022-06-06 03:45:00     [False, True, True, True]        4.951019   
2022-06-06 04:00:00     [False, True, True, True]        7.078754   
2022-06-06 04:15:00     [False, True, True, True]        6.430890   
2022-06-06 04:30:00     [False, True, True, True]        6.301700   

                     ev_discharged_pwr          load  load_reward   EV_reward  \
time                                                                            
2022-01-01 00:00:00                0.0 -3.509061e+00    -4.932836    0.000000   
2022-01-01 00:15:00                0.0 -3.959702e+00    -5.171164    0.000000   
2022-01-01 00:30:00                0.0 -4.188280e+00    -3.765360    0.000000   
2022-01-01 00:45:00                0.0 -3.259216e+00    -6.189821    0.000000   
2022-01-01 01:00:00                0.0 -5.308803e+00    -6.335598    0.000000   
...                                ...           ...          ...         ...   
2022-06-06 03:30:00               -1.0  0.000000e+00    15.000000 -127.155959   
2022-06-06 03:45:00               -1.0 -4.440892e-16    15.000000    0.000000   
2022-06-06 04:00:00                0.0  0.000000e+00    15.000000    0.000000   
2022-06-06 04:15:00                0.0  0.000000e+00    15.000000    0.000000   
2022-06-06 04:30:00                0.0  0.000000e+00    15.000000    0.000000   

                        rewards  
time                             
2022-01-01 00:00:00   -4.932836  
2022-01-01 00:15:00   -5.171164  
2022-01-01 00:30:00   -3.765360  
2022-01-01 00:45:00   -6.189821  
2022-01-01 01:00:00   -6.335598  
...                         ...  
2022-06-06 03:30:00 -112.155959  
2022-06-06 03:45:00   15.000000  
2022-06-06 04:00:00   15.000000  
2022-06-06 04:15:00   15.000000  
2022-06-06 04:30:00   15.000000  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
#env.close()